#Objective

#Notebook Initialization

##Import Packages

In [0]:
from pyspark.sql.functions import col,isnan,when,count,lit, to_date,lpad,date_format,rpad,regexp_replace,concat,to_utc_timestamp,to_timestamp, countDistinct,unix_timestamp, row_number, when
from pyspark.sql.types import IntegerType,BooleanType,DateType,StringType,TimestampType
from pyspark.sql import DataFrameNaFunctions
from pyspark import StorageLevel
import pandas as pd
import seaborn as sns
import numpy as np
import matplotlib.pyplot as plt
from pytz import timezone
import datetime
from pyspark.ml import Pipeline, PipelineModel
from pyspark.ml.feature import StringIndexer, VectorAssembler, OneHotEncoder, StandardScaler, PCA, VectorSlicer, Imputer
from pyspark.ml.linalg import Vectors
from pyspark.sql.functions import percent_rank
from pyspark.sql import Window
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier, GBTClassifier, DecisionTreeClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
from pyspark.sql import functions as f

##Cloud Storage Parameters

In [0]:
blob_container = "tm30container" # The name of your container created in https://portal.azure.com
storage_account = "w261tm30" # The name of your Storage account created in https://portal.azure.com
secret_scope = "w261tm30" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "tm30key" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

test_pq = spark.read.parquet(f"{blob_url}/2022-03-24_data_chkpt_PQ_full")

##Define Functions

In [0]:
def data_pull(df, time_window = 'full', date_col='FLIGHT_UTC_DATE'):
    """Pull processed dataset"""
    if time_window == '2019':
        df = df.filter(f.year(col(date_col)) == 2019)
    elif time_window == '2018':
        df = df.filter(f.year(col(date_col)) == 2018)
    elif time_window == '2017':
        df = df.filter(f.year(col(date_col)) == 2017)
    elif time_window == '2016':
        df = df.filter(f.year(col(date_col)) == 2016) 
    
    #The commands below are for 2015 data
    elif time_window == '6m':
        df = df.filter(col(date_col) < "2015-07-01T00:00:00.000")  
    elif time_window == '3m':
        df = df.filter(col(date_col) < "2015-04-01T00:00:00.000")
        #comment this out if it takes too long
    
    print(f'{df.count():,} total records imported for the {time_window} dataset')
    return df

In [0]:
def pre_pipeline(index_cols, cont_cols, cat_cols, pred_cols):
    ''' This function creates a pre-processed pipeline to be used to prepare for crossfold validation and model training
    '''
    pre_pipeline = None
    
    #Convert string to index
    indexer = StringIndexer(inputCols=cat_cols, outputCols=[c+"_idx" for c in cat_cols]).setHandleInvalid("keep")

    #Convert categorical columns to index
    encoder = OneHotEncoder(inputCols=[c+"_idx" for c in cat_cols], outputCols= [c+"_OHE" for c in cat_cols])
    
    #Vector assembler for categorical
    assembler_cat = VectorAssembler(inputCols= [x+"_OHE" for x in cat_cols], outputCol="cat_features")

    #Ensure continuous variables have values
    imputer = Imputer(inputCols=cont_cols, outputCols=cont_cols)
        
    assembler_lab = StringIndexer(inputCol='DEP_DEL15', outputCol="label")
        
    pre_pipeline = Pipeline(stages=[indexer, encoder, assembler_cat, imputer, assembler_lab])
    
    return pre_pipeline

In [0]:
def scaled_pipeline(model):
    ''' This function creates a scaled processed and scaled pipeline to be used to train models.
        Parameters:
            model:    lr = Logistic Regression;
                      rf = Random Forest 
                      dt = Decision Trees
        Returns: a pipeline model
    '''
    pipeline_model = None
    
    #Assemble cont variables
    assembler_num = VectorAssembler(inputCols=cont_cols, outputCol="scale_nums")
    
    #Scale the values
    scaler = StandardScaler(inputCol="scale_nums", outputCol="scaledFeatures", withStd=True, withMean=True)

    #Vector assembler combined
    assembler = VectorAssembler(inputCols=["scaledFeatures", "cat_features"], outputCol="features")
    
    #Models for the pipeline
    if model == 'lr':
        
        class_model = LogisticRegression(featuresCol = 'features', labelCol = 'label', threshold=0.7)
        
    elif model == 'rf':
        
        class_model = RandomForestClassifier(featuresCol = 'features', labelCol = 'label')
        
    elif model == 'dt':
        class_model = DecisionTreeClassifier(featuresCol = 'features', labelCol = 'label')
        
    pipeline_model = Pipeline(stages=[assembler_num, scaler, assembler, class_model])
    
    return pipeline_model

In [0]:
def custom_CV(df_rank, pre_pipeline, class_model, sample, kfolds):

    #Create evaluation metric lists
    f_5_score_list_CV_average = []
    
    # Create Time Splits
    splits = 1.0/(kfolds + 1)
    cutoff = splits
    
    #Preprocess Pipleine
    fit_df = pre_pipeline.fit(df_rank)
    transform_df = fit_df.transform(df_rank).persist(StorageLevel.MEMORY_AND_DISK)

                
    f_5_score_list = []
    scaled_pipelines = scaled_pipeline('lr')
                    
    for split in range(kfolds):
                        
        train_df = transform_df.where(f"rank <= {cutoff}").cache()
        test_df = transform_df.where(f"rank > {cutoff} and rank <= {cutoff+splits}").cache()
        cutoff += splits

        if sample == 'down':
             train_df = downsample(train_df)
                    
                        #Generate model 
        model = scaled_pipelines.fit(train_df)
        predict = model.transform(test_df)

                        #Calculate evaluation metrics
        evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
        f_5 = evaluatorf_5.evaluate(predict)
        f_5_score_list.append(f_5)
    
    transform_df.unpersist()
    return predict, np.mean(f_5_score_list)

In [0]:
def downsample(train_df):
    '''Downsample minority class to balance classes. 
    Only works if delay count is less than on_time count (should be the case...)'''
    
    delay_count = train_df.filter(col("label") == 1).count()
    on_time_count = train_df.filter(col("label") == 0).count()
    
    total_count = delay_count + on_time_count
    delay_pct = delay_count / on_time_count
    
    train_delay = train_df.filter(col('label') == 1)
    train_on_time = train_df.filter(col('label') == 0).sample(withReplacement=False, fraction = delay_pct, seed= 2022)
    train_downsampled = train_delay.union(train_on_time)
    
    return train_downsampled

#Pipeline Initialization

In [0]:
#Last minute data curation...
test_pq = test_pq.na.replace('', None, 'wnd_type')\
            .na.replace('', None, 'ga1_cld')\
            .na.replace('', None, 'ga1_cov')\
            .withColumn('wnd_dir_angle',col('wnd_dir_angle').cast(IntegerType()))\
            .withColumn('ka1_temp', when(f.isnull('ka1_temp'), '0').when(f.col('ka1_temp') < 0, -1).otherwise('1'))\
            .withColumn('FLIGHT_ROUTE', concat(col('ORIGIN'),lit("-"),col('DEST')))

df_2015_2018 = test_pq.filter(col('FLIGHT_UTC_DATE') < "2019-01-01T00:00:00.000")

df_6m = data_pull(test_pq, time_window='6m', date_col='FLIGHT_UTC_DATE')

df_3m = data_pull(test_pq, time_window='3m', date_col='FLIGHT_UTC_DATE')

df_small_test = test_pq.filter(col('FLIGHT_UTC_DATE') < "2015-02-01T00:00:00.000")

df_2019 = data_pull(test_pq, time_window='2019', date_col='FLIGHT_UTC_DATE')

3,365,522 total records imported for the 6m dataset
1,630,806 total records imported for the 3m dataset
8,539,842 total records imported for the 2019 dataset

In [0]:
df_2015_2018.select('FLIGHT_ROUTE').distinct().count()

Out[50]: 6168

In [0]:
df_small_test = test_pq.filter(col('FLIGHT_UTC_DATE') < "2015-03-01T00:00:00.000")

In [0]:
(df_small_test.count(), len(df_small_test.columns))

Out[10]: (1043680, 100)

##Chosen Model Columns

In [0]:
index_cols = ['UNIQUE_ID','FLIGHT_UTC_DATE', 'rank']

cat_cols = ['TIME_OF_DAY', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'wnd_type', 'cig_ceil_is_qual', 'tmp_air_is_qual',  'slp_prs_is_qual', 'ga1_cov','ga1_cld', 'ga1_bs_ht_is_qual', 'wnd_spd_is_qual', 'ga1_cld_qual', 'dew_pnt_is_qual', 'ga1_cov_is_qual', 'aa1_is_qual', 'vis_dist_is_qual', 'ka1_temp', 'FLIGHT_ROUTE']


cont_cols = ['ELEVATION', 'wnd_dir_angle', 'wnd_spd_rate', 'cig_ceil_ht', 'vis_dist', 'tmp_air', 'dew_pnt_tmp','slp_prs', 'aa1_prd_quant_hr', 'aa1_dp', 'ga1_bs_ht']

pred_cols = ['DEP_DEL15']

##Test Pipeline Function

In [0]:
df_test = df_6m.filter(col('FLIGHT_UTC_DATE') < "2015-02-01T00:00:00.000")
df_test.count()

Out[42]: 551886

In [0]:
df_validate = df_6m.filter((col('FLIGHT_UTC_DATE') > "2015-02-01T00:00:00.000") &\
                          (col('FLIGHT_UTC_DATE') < "2015-04-01T00:00:00.000"))

df_validate.count()

Out[43]: 1078821

In [0]:
display(df_test)

In [0]:
pre_pipe_test = pre_pipeline(index_cols, cont_cols, cat_cols, pred_cols)

fit_test = pre_pipe_test.fit(df_test)
transform_test = fit_test.transform(df_test)

df_test_ds = downsample(transform_test)
# display(df_test_ds)

'param_grid'

In [0]:
param_grid = {'maxIter': 1, 'regParam': 0, 'elasticNetParam': .5}
scaled_pipelines = scaled_pipeline('lr', param_grid)

test_model = scaled_pipelines.fit(df_test_ds)

In [0]:
transform_validate = fit_test.transform(df_validate)

transform = test_model.transform(transform_validate)

In [0]:
#calcuate f Score
evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
f_5 = evaluatorf_5.evaluate(transform)

print('F Score: {:3f}\nParam Grid: {}'.format(f_5, param_grid.items()))

F Score: 0.383108
Param Grid: dict_items([('maxIter', 1), ('regParam', 0), ('elasticNetParam', 0)])

In [0]:
#calcuate f Score
evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
f_5 = evaluatorf_5.evaluate(transform)

print('F Score: {:3f}\nParam Grid: {}'.format(f_5, param_grid.items()))

F Score: 0.388877
Param Grid: dict_items([('maxIter', 1), ('regParam', 0), ('elasticNetParam', 0.5)])

##Test Crossfold Pipeline

In [0]:
# Create Time Splits
splits = 1/(5 + 1)
cutoff += splits 

train_df_split = train_test_window.where(f"rank <= {cutoff}").cache()
test_df = train_test_window.where(f"rank > {cutoff} and rank <= {cutoff+splits}").cache()

In [0]:
#Initialize Pre-processing Pipeline
pre_pipe = pre_pipeline(index_cols, cont_cols, cat_cols, pred_cols)

In [0]:
fit_test = pre_pipe.fit(train_df_split)
transform_test = fit_test.transform(train_df_split)

df_test_ds = downsample(transform_test)

In [0]:
param_grid = {'maxIter': 1, 'regParam': 0, 'elasticNetParam': .5}
scaled_pipelines = scaled_pipeline('lr', param_grid)

test_model = scaled_pipelines.fit(df_test_ds)

In [0]:
transform_validate = fit_test.transform(test_df)

transform = test_model.transform(transform_validate)

In [0]:
#calcuate f Score
evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
f_5 = evaluatorf_5.evaluate(transform)

print('F Score: {:3f}\nParam Grid: {}'.format(f_5, param_grid.items()))

#Create Baseline Models

In [0]:
#Modify to switch from test to scaled up model
df_model = df_small_test

In [0]:
#Add rank to allow forx custom crossvalidation and windowing
train_test_window = df_model.withColumn("rank", percent_rank().over(Window.partitionBy().orderBy("FLIGHT_UTC_DATE")))

In [0]:
# #Create pipeline for Logistic Regression
# lr_model = scaled_pipeline('lr')

# #Create pipeline for Random Forest Classification
# rf_model = scaled_pipeline('rf')

# #Create pipeline for Decision Tree Classification
# dt_model = scaled_pipeline('dt')

##Logistic Regression Pipeline

In [0]:
df_predict, f_5 = custom_CV(train_test_window, pre_pipe, 'lr', 'down', 5)

In [0]:
f_5

Out[49]: 0.32745626219647145

In [0]:
display(df_predict)

UNIQUE_ID FLIGHT_UTC_DATE WEATHER_UTC_DATE TIME_OF_DAY STATION NAME MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER TAIL_NUM ORIGIN DEST DEP_DEL15 DEP_DELAY_NEW ARR_DELAY_NEW CRS_ELAPSED_TIME SOURCE LATITUDE LONGITUDE ELEVATION CALL_SIGN wnd_dir_angle wnd_dir_qual wnd_type wnd_spd_rate wnd_spd_qual wnd_ex wnd_dir_is_qual wnd_spd_is_qual cig_ceil_ht cig_ceil_qual cig_ceil_det cig_cavok cig_ex cig_cavok_bool cig_ceil_is_qual vis_dist vis_dist_qual vis_dist_var vis_dist_qual_var vis_ex vis_dist_var_bool vis_dist_is_qual vis_dist_is_qual_var tmp_air tmp_air_qual tmp_ex tmp_air_is_qual dew_pnt_tmp dew_pnt_qual dew_ex dew_pnt_is_qual slp_prs slp_prs_qual slp_ex slp_prs_is_qual aa1_prd_quant_hr aa1_dp aa1_cond aa1_qual aa1_ex aa1_is_qual aj1_dim aj1_cond aj1_qual aj1_eq_wtr_dp aj1_eq_wtr_cond aj1_eq_wtr_cond_qual aj1_ex aj1_is_qual aj1_eq_wtr_cond_is_qual ga1_cov ga1_cov_qual ga1_bs_ht ga1_bs_ht_qual ga1_cld ga1_cld_qual ga1_ex ga1_cov_is_qual ga1_bs_ht_is_qual ka1_prd_quant ka1_code ka1_temp ka1_temp_qual ka1_ex ka1_temp_is_qual at1_src_elem at1_wthr at1_wthr_abrv at1_qual at1_ex at1_is_qual ax1_atm ax1_qual ax1_prd_quant ax1_prd_qual ax1_ex ax1_is_qual ax1_prd_is_qual FLIGHT_ROUTE rank TIME_OF_DAY_idx MONTH_idx DAY_OF_WEEK_idx OP_UNIQUE_CARRIER_idx wnd_type_idx cig_ceil_is_qual_idx tmp_air_is_qual_idx slp_prs_is_qual_idx ga1_cov_idx ga1_cld_idx ga1_bs_ht_is_qual_idx wnd_spd_is_qual_idx ga1_cld_qual_idx dew_pnt_is_qual_idx ga1_cov_is_qual_idx aa1_is_qual_idx vis_dist_is_qual_idx ka1_temp_idx FLIGHT_ROUTE_idx TIME_OF_DAY_OHE MONTH_OHE DAY_OF_WEEK_OHE OP_UNIQUE_CARRIER_OHE wnd_type_OHE cig_ceil_is_qual_OHE tmp_air_is_qual_OHE slp_prs_is_qual_OHE ga1_cov_OHE ga1_cld_OHE ga1_bs_ht_is_qual_OHE wnd_spd_is_qual_OHE ga1_cld_qual_OHE dew_pnt_is_qual_OHE ga1_cov_is_qual_OHE aa1_is_qual_OHE vis_dist_is_qual_OHE ka1_temp_OHE FLIGHT_ROUTE_OHE cat_features label scale_nums scaledFeatures features rawPrediction probability prediction AA-1301-2015-01-26 08:21:00 2015-01-26T14:21:00.000+0000 2015-01-26T11:53:00.000+0000 Morning 72658014922 MINNEAPOLIS ST PAUL INTERNATIONAL AIRPORT, MN US JAN MONDAY AA N528AA MSP DFW 0 0 0 164 7 44.8831 -93.2289 265.8 KMSP 150 5 N 46 5 1 1 1 335 5 M N 1 1 1 16093 5 N 5 1 1 1 1 -28 5 1 1 -50 5 1 1 10084 5 1 1 1 0 5 1 1 3 5 250 9 1 1 1 08 5 335 5 null 1 1 1 1 60 M -1 1 1 1 null null null null 1 1 null null null null 1 1 1 MSP-DFW 0.8333819545738695 0.0 0.0 2.0 4.0 0.0 0.0 0.0 0.0 2.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 408.0 Map(vectorType -> sparse, length -> 4, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 7, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 13, indices -> List(4), values -> List(1.0)) Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 7, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 3, indices -> List(), values -> List()) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 3, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 3870, indices -> List(408), values -> List(1.0)) Map(vectorTyp

In [0]:
df_predict.groupBy('label', 'prediction').count().show()

+-----+----------+-----+
label|prediction|count|
+-----+----------+-----+
 0.0| 0.0|77346|
 1.0| 0.0|11930|
 0.0| 1.0| 1411|
 1.0| 1.0| 1268|
+-----+----------+-----+

In [0]:
FN = df_predict.filter('prediction = 0 AND label <> prediction')

In [0]:
display(FN)

UNIQUE_ID FLIGHT_UTC_DATE WEATHER_UTC_DATE TIME_OF_DAY STATION NAME MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER TAIL_NUM ORIGIN DEST DEP_DEL15 DEP_DELAY_NEW ARR_DELAY_NEW CRS_ELAPSED_TIME SOURCE LATITUDE LONGITUDE ELEVATION CALL_SIGN wnd_dir_angle wnd_dir_qual wnd_type wnd_spd_rate wnd_spd_qual wnd_ex wnd_dir_is_qual wnd_spd_is_qual cig_ceil_ht cig_ceil_qual cig_ceil_det cig_cavok cig_ex cig_cavok_bool cig_ceil_is_qual vis_dist vis_dist_qual vis_dist_var vis_dist_qual_var vis_ex vis_dist_var_bool vis_dist_is_qual vis_dist_is_qual_var tmp_air tmp_air_qual tmp_ex tmp_air_is_qual dew_pnt_tmp dew_pnt_qual dew_ex dew_pnt_is_qual slp_prs slp_prs_qual slp_ex slp_prs_is_qual aa1_prd_quant_hr aa1_dp aa1_cond aa1_qual aa1_ex aa1_is_qual aj1_dim aj1_cond aj1_qual aj1_eq_wtr_dp aj1_eq_wtr_cond aj1_eq_wtr_cond_qual aj1_ex aj1_is_qual aj1_eq_wtr_cond_is_qual ga1_cov ga1_cov_qual ga1_bs_ht ga1_bs_ht_qual ga1_cld ga1_cld_qual ga1_ex ga1_cov_is_qual ga1_bs_ht_is_qual ka1_prd_quant ka1_code ka1_temp ka1_temp_qual ka1_ex ka1_temp_is_qual at1_src_elem at1_wthr at1_wthr_abrv at1_qual at1_ex at1_is_qual ax1_atm ax1_qual ax1_prd_quant ax1_prd_qual ax1_ex ax1_is_qual ax1_prd_is_qual FLIGHT_ROUTE rank TIME_OF_DAY_idx MONTH_idx DAY_OF_WEEK_idx OP_UNIQUE_CARRIER_idx wnd_type_idx cig_ceil_is_qual_idx tmp_air_is_qual_idx slp_prs_is_qual_idx ga1_cov_idx ga1_cld_idx ga1_bs_ht_is_qual_idx wnd_spd_is_qual_idx ga1_cld_qual_idx dew_pnt_is_qual_idx ga1_cov_is_qual_idx aa1_is_qual_idx vis_dist_is_qual_idx ka1_temp_idx FLIGHT_ROUTE_idx TIME_OF_DAY_OHE MONTH_OHE DAY_OF_WEEK_OHE OP_UNIQUE_CARRIER_OHE wnd_type_OHE cig_ceil_is_qual_OHE tmp_air_is_qual_OHE slp_prs_is_qual_OHE ga1_cov_OHE ga1_cld_OHE ga1_bs_ht_is_qual_OHE wnd_spd_is_qual_OHE ga1_cld_qual_OHE dew_pnt_is_qual_OHE ga1_cov_is_qual_OHE aa1_is_qual_OHE vis_dist_is_qual_OHE ka1_temp_OHE FLIGHT_ROUTE_OHE cat_features label scale_nums scaledFeatures features rawPrediction probability prediction US-1931-2015-01-26 09:25:00 2015-01-26T14:25:00.000+0000 2015-01-26T11:52:00.000+0000 Morning 72314013881 CHARLOTTE DOUGLAS AIRPORT, NC US JAN MONDAY US N754UW CLT MEM 1 15 7 112 7 35.2236 -80.9552 221.9 KCLT 150 5 N 21 5 1 1 1 22000 5 N 1 1 1 16093 5 N 5 1 1 1 1 44 5 1 1 0 5 1 1 10037 5 1 1 1 0 5 1 1 null null null null null null 1 1 1 04 5 2591 5 null 1 1 1 1 60 M 1 1 1 1 null null null null 1 1 null null null null 1 1 1 CLT-MEM 0.8334109461210216 0.0 0.0 2.0 6.0 0.0 0.0 0.0 0.0 3.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 1917.0 Map(vectorType -> sparse, length -> 4, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 7, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 13, indices -> List(6), values -> List(1.0)) Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 7, indices -> List(3), values -> List(1.0)) Map(vectorType -> sparse, length -> 3, indices -> List(), values -> List()) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 3, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 3870, indices -> List(1917), values -> List(1.0)) Map(vecto

##Decision Tree Pipeline

In [0]:
Eval_dt, metric_dt, best_model_dt = custom_CV(train_test_window, pre_pipe, dt_model, 'down', 5)

----- Completed fold 1.000000 -----
----- Completed fold 2.000000 -----
----- Completed fold 3.000000 -----
----- Completed fold 4.000000 -----
----- Completed fold 5.000000 -----

In [0]:
Eval_dt

Out[84]:

K-Fold 
 F_0.5 Score 
 Recall 
 Precision 
 
 
 
 
 0 
 1 
 0.266504 
 0.657183 
 0.232021 
 
 
 1 
 2 
 0.311281 
 0.653145 
 0.275262 
 
 
 2 
 3 
 0.317414 
 0.675540 
 0.280269 
 
 
 3 
 4 
 0.301232 
 0.659018 
 0.265233 
 
 
 4 
 5 
 0.321497 
 0.689491 
 0.283650

##Random Forest Pipeline

In [0]:
Eval_rf, metric_rf, best_model_rf = custom_CV(train_test_window, pre_pipe, rf_model, 'down', 5)

----- Completed fold 1.000000 -----
----- Completed fold 2.000000 -----
----- Completed fold 3.000000 -----
----- Completed fold 4.000000 -----
----- Completed fold 5.000000 -----

In [0]:
Eval_rf

Out[86]:

K-Fold 
 F_0.5 Score 
 Recall 
 Precision 
 
 
 
 
 0 
 1 
 0.262586 
 0.617124 
 0.229608 
 
 
 1 
 2 
 0.304598 
 0.652695 
 0.268764 
 
 
 2 
 3 
 0.313122 
 0.642113 
 0.277569 
 
 
 3 
 4 
 0.302325 
 0.594569 
 0.269240 
 
 
 4 
 5 
 0.319489 
 0.694610 
 0.281485

##Test on unseen data

In [0]:
pre_pipeline = pre_pipe.fit(df_model)
transform_2019 = pre_pipeline.transform(df_2019)

In [0]:
lr_pred_2019 = best_model_lr.transform(transform_2019)

In [0]:
#calcuate f Score
lr_evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
lr_f_5 = lr_evaluatorf_5.evaluate(lr_pred_2019)

lr_evaluator_recall = MulticlassClassificationEvaluator(metricName='recallByLabel', metricLabel=1)
lr_recall = lr_evaluator_recall.evaluate(lr_pred_2019)

lr_evaluator_precision = MulticlassClassificationEvaluator(metricName='precisionByLabel', metricLabel=1)
lr_precision = lr_evaluator_precision.evaluate(lr_pred_2019)

print('F Score: {:3f}\nRecall: {:3f}\nPrecision  {:3f}'.format(lr_f_5, lr_recall, lr_precision))

F Score: 0.334221
Recall: 0.629899
Precision 0.299119

In [0]:
dt_pred_2019 = best_model_dt.transform(transform_2019)

In [0]:
#calcuate f Score
dt_evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
dt_f_5 = dt_evaluatorf_5.evaluate(dt_pred_2019)

dt_evaluator_recall = MulticlassClassificationEvaluator(metricName='recallByLabel', metricLabel=1)
dt_recall = dt_evaluator_recall.evaluate(dt_pred_2019)

dt_evaluator_precision = MulticlassClassificationEvaluator(metricName='precisionByLabel', metricLabel=1)
dt_precision = dt_evaluator_precision.evaluate(dt_pred_2019)

print('F Score: {:3f}\nRecall: {:3f}\nPrecision  {:3f}'.format(dt_f_5, dt_recall, dt_precision))

F Score: 0.316191
Recall: 0.662079
Precision 0.279665

In [0]:
rf_pred_2019 = best_model_rf.transform(transform_2019)

In [0]:
#calcuate f Score
rf_evaluatorf_5 = MulticlassClassificationEvaluator(metricName='fMeasureByLabel', metricLabel=1, beta=0.5)
rf_f_5 = rf_evaluatorf_5.evaluate(rf_pred_2019)

rf_evaluator_recall = MulticlassClassificationEvaluator(metricName='recallByLabel', metricLabel=1)
rf_recall = rf_evaluator_recall.evaluate(rf_pred_2019)

rf_evaluator_precision = MulticlassClassificationEvaluator(metricName='precisionByLabel', metricLabel=1)
rf_precision = rf_evaluator_precision.evaluate(rf_pred_2019)

print('F Score: {:3f}\nRecall: {:3f}\nPrecision  {:3f}'.format(rf_f_5, rf_recall, rf_precision))

F Score: 0.312406
Recall: 0.667875
Precision 0.275719

#References

 - https://machinelearningmastery.com/k-fold-cross-validation/
 - https://www.analyticsvidhya.com/blog/2019/11/build-machine-learning-pipelines-pyspark/
 - https://medium.com/@junwan01/oversampling-and-undersampling-with-pyspark-5dbc25cdf253